In [1]:
!pip install -q -U pandarallel

In [ ]:
import pandas as pd
import numpy as np
from sklearn.metrics.pairwise import cosine_similarity
from ast import literal_eval
from tqdm import tqdm
from pandarallel import pandarallel

pandarallel.initialize(progress_bar=True)
path = "/kaggle/input/week18-generate-emb-csv/earnings_calls_cleaned_metadata_keywords_indices.csv"
data = pd.read_csv(path)
print(data.columns)
data["Embedding"] = data["Embedding"].parallel_apply(literal_eval)

# Iterate over the text column in a rolling window of 3 rows


def compute_rolling_text_sim(df, similarity_thresh=0.75):

    columns = [
        "Text",
        "Name",
        "Company",
        "Position",
        "Year",
        "Month",
        "Date",
        "Ticker",
        "Section",
        "Quarter",
        "Participant_Type",
        "Paragraph_id",
        "File_Name",
        "Sentence_id",
        "QA_Flag",
        # "Embedding",
    ]



    new_df = pd.DataFrame(columns=columns)

    for i in tqdm(range(len(df) - 2)):
        first_row_embedding = df.loc[i, "Embedding"]
        sec_row_embedding = df.loc[i + 1, "Embedding"]
        third_row_embedding = df.loc[i + 2, "Embedding"]
        similarity_1 = cosine_similarity(first_row_embedding, sec_row_embedding)[0][0]
        similarity_2 = cosine_similarity(sec_row_embedding, third_row_embedding)[0][0]

        first_row_paragraph_id = df.loc[i, "Paragraph_id"]
        second_row_paragraph_id = df.loc[i + 1, "Paragraph_id"]
        third_row_paragraph_id = df.loc[i + 2, "Paragraph_id"]

        first_row_filename = df.loc[i, "File_Name"]
        second_row_filename = df.loc[i + 1, "File_Name"]
        third_row_filename = df.loc[i + 2, "File_Name"]

        # print((similarity_1, similarity_2))

        first_row_text = df.loc[i, "Text"]
        second_row_text = df.loc[i + 1, "Text"]
        third_row_text = df.loc[i + 2, "Text"]

        new_text = ""
        new_row = df.loc[i, columns]

        if (
            (similarity_1 >= similarity_thresh)
            and first_row_filename == second_row_filename
            and first_row_paragraph_id == second_row_paragraph_id
        ):
            new_text = first_row_text + " " + second_row_text

            if similarity_2 >= similarity_thresh:
                new_text = first_row_text + " " + second_row_text + " " + third_row_text
            else:
                new_text = first_row_text + " " + second_row_text
        else:
            new_text = first_row_text

        new_row["Text"] = new_text
        new_df = new_df.append(new_row, ignore_index=True)

    return new_df


test_df = compute_rolling_text_sim(data)
print(test_df.head(20))

test_df.to_csv("test_df.csv", index=False)


INFO: Pandarallel will run on 2 workers.
INFO: Pandarallel will use Memory file system to transfer data between the main process and workers.
Index(['Text', 'Name', 'Company', 'Position', 'Year', 'Month', 'Date',
       'Ticker', 'Section', 'Quarter', 'Participant_Type', 'Paragraph_id',
       'File_Name', 'Sentence_id', 'QA_Flag', 'Embedding'],
      dtype='object')


  0%|          | 0/58783 [00:00<?, ?it/s]/tmp/ipykernel_32/3138079657.py:81: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_df = new_df.append(new_row, ignore_index=True)
/tmp/ipykernel_32/3138079657.py:81: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_df = new_df.append(new_row, ignore_index=True)
/tmp/ipykernel_32/3138079657.py:81: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_df = new_df.append(new_row, ignore_index=True)
/tmp/ipykernel_32/3138079657.py:81: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_df = new_df.append(new_row, ignore_index=True)
/tmp/ipykernel_32/3138079657.py:81: FutureWarning: The frame.append met